In [ ]:
# ..... get pseudobulk matrices across stages ..... #

In [2]:
library(Seurat)
library(SingleCellExperiment)
library(MetaMarkers)

In [32]:
# get pseudo-bulk for CPM data
get_cpm_pseudo_bulk <- function(scdata, ctype_list){      
        
    new_labels = scdata$ctypes
    sc_sub2 = matrix(NA, nrow = dim(scdata)[1], ncol = length(ctype_list))
    
    for (i in 1:length(ctype_list)){
        cols = which(new_labels==ctype_list[i])
        
        if(length(cols)>1){
            sc_sub2[,i] = rowSums(cpm(scdata)[,cols])/length(cols)
        }else if(length(cols)==1){            
            sc_sub2[,i] = cpm(scdata)[,cols]
        }else{
            sc_sub2[,i] = 0
        }
    }    
    rownames(sc_sub2) = rownames(scdata)
    colnames(sc_sub2) = ctype_list
    return(sc_sub2)
}

In [4]:
# cell type order
# ctype_order = c('vCM', 'aCM', 'immature-CM', 'endothelial', 'endocardial', 'epicardial',
                # 'fibroblast', 'SMC', 'pericyte', 'neural-crest', 'blood', 'macrophage')

ctype_order = c('LV_vCM', 'RV_vCM', 'aCM', 'immature_CM', 'endocardial', 'epicardial',
                'mes_progenitor', 'fibroblast', 'SMC', 'neural_crest', 'blood', 'macrophage')
length(ctype_order)

[1] 12

In [11]:
# load integrated data
sc1 = readRDS('chicken_integrated_ssSTACAS.rds')
DefaultAssay(sc1) <- 'RNA'

# get harmonised labels
tab1 = read.delim('chicken_ssSTACAS_celltypes.txt', sep = '\t')
tab1[1,]

sc1$stage = sc1$orig.ident
sc1$broad_type = tab1$subtype[match(sc1$seurat_clusters, tab1$cluster)]
sc1$cluster = tab1$label[match(sc1$seurat_clusters, tab1$cluster)]
sc1$ctypes <- sc1$cluster  # sub('\\_.*', '', sc1$cluster)
# sc1$ctypes[sc1$ctypes=='immature-blood'] = 'blood'
sc1@meta.data[1,]

species cluster celltype subtype label cluster_new
1 chicken 0       Myeloid  blood   blood c1

orig.ident nCount_RNA nFeature_RNA species
stage23_sample3_AAACCCAAGTAACAGT-1 stage23    5044       2506         chicken
                                   dataset         consensus_type  
stage23_sample3_AAACCCAAGTAACAGT-1 stage23_sample3 Endothelial_cell
                                   integrated_snn_res.1 seurat_clusters stage  
stage23_sample3_AAACCCAAGTAACAGT-1 12                   12              stage23
                                   broad_type  cluster     ctypes     
stage23_sample3_AAACCCAAGTAACAGT-1 endocardial endocardial endocardial

In [12]:
# make SCE object
sce2 = SingleCellExperiment(list(counts = sc1@assays$RNA@counts), colData = DataFrame(sc1@meta.data))
assay(sce2, "cpm") = convert_to_cpm(assay(sce2))
sce2

class: SingleCellExperiment 
dim: 17007 50547 
metadata(0):
assays(2): counts cpm
rownames(17007): SPRY2 PCDH20 ... ENSGALG00010000495 ENSGALG00010000377
rowData names(0):
colnames(50547): stage23_sample3_AAACCCAAGTAACAGT-1
  stage23_sample3_AAACCCACAACAGAGC-1 ...
  stage32_sample12_TTTGTTGCACAAGTGG-1
  stage32_sample12_TTTGTTGGTAGACGGT-1
colData names(12): orig.ident nCount_RNA ... cluster ctypes
reducedDimNames(0):
mainExpName: NULL
altExpNames(0):

In [33]:
# create pseudo-bulk matrices for all genes
scbulk1 = get_cpm_pseudo_bulk(sce2[,sce2$stage=='stage23'], ctype_order)
scbulk2 = get_cpm_pseudo_bulk(sce2[,sce2$stage=='stage28'], ctype_order)
scbulk3 = get_cpm_pseudo_bulk(sce2[,sce2$stage=='stage32'], ctype_order)

scbulk1[c('TBX5','COL3A1'),]

LV_vCM    RV_vCM    aCM       immature_CM endocardial epicardial
TBX5   458.29857 364.05501 697.04466 189.76442   44.24657     70.06091 
COL3A1  43.08104  48.17911  51.49619  61.29825   47.78075    259.19962 
       mes_progenitor fibroblast SMC       neural_crest blood    macrophage
TBX5   46.01174       85.42308     9.61893 0            52.83836 11.99288  
COL3A1 89.49334       81.12275   258.24150 0            18.94065 10.79226

In [34]:
# save
save(scbulk1, scbulk2, scbulk3, file = 'chicken_integrated_pseudobulk_expression_matrices.Rdata')

In [35]:
colnames(scbulk1) <- paste0('s1|', colnames(scbulk1))
colnames(scbulk2) <- paste0('s2|', colnames(scbulk2))
colnames(scbulk3) <- paste0('s3|', colnames(scbulk3))

dfnew = cbind(scbulk1, scbulk2, scbulk3)

# save
save(dfnew, file = 'chicken_full_integrated_pseudobulk_expression_matrix.Rdata')